In [35]:
import pandas as pd
import numpy as np
import datetime as dt
import re
import requests
import plotly.express as px
import plotly.graph_objects as go
from plotly.subplots import make_subplots

In [4]:
async def Load():
    async with aiohttp.ClientSession() as session:
        async with session.get(url) as response:
            response


In [5]:
import requests

In [6]:
url = "https://www.climatewatchdata.org/api/v1/data/ndc_content/"
response = requests.get(url).json()
datos = response['data']

In [7]:
dataset_cancer = pd.read_csv(r"C:\Users\ferch\Desktop\Henry\Proyecto Grupal\CO2-Emissions\datasets\enfermedades\casos_cancer_pulmon_fym_NORMALIZADO.csv",sep=';')
dataset_co2 = pd.read_csv(r"C:\Users\ferch\Desktop\Henry\Proyecto Grupal\CO2-Emissions\datasets\energyco2_normalizado.csv",sep=',')

In [8]:
df_cancer = pd.DataFrame(dataset_cancer)
df_co2 = pd.DataFrame(dataset_co2)
col = 'Unnamed: 0'

In [9]:
df_cancer.drop(columns=col,inplace=True)
df_co2.drop(columns=col,inplace=True)

In [10]:
df_co2.rename(columns={'co2_emision_co2':'co2'},inplace=True)

In [11]:
df_cancer = df_cancer.merge(df_co2,on=['pais','anio'])

In [12]:
df_cancer = df_cancer[df_cancer['energia_tipo']=='all_energy_types']

In [13]:
paises = ['United States', 'China', 'Russia', 'Saudi Arabia', 'Canada']
cols = ['pais','anio','casos F','Casos M','energia_produccion','co2']

In [14]:
df2 = df_cancer[cols]

In [15]:
df2.head()

pais  anio  casos F  Casos M  energia_produccion     co2
0            Afghanistan  1989      139      809                0.12    6.06
6                 Angola  1989       84      490                0.99    4.90
12               Albania  1989      104      518                0.19    9.95
18  United Arab Emirates  1989       12       50                4.99   73.50
24             Argentina  1989     1750     8320                1.99  108.46

In [16]:
df_cancerTOP = df2[df_cancer['pais'].isin(paises)]

In [17]:
df3 = df_cancerTOP.groupby(by='pais').sum().reset_index()

In [18]:
df3['casos'] = df3['casos F'] + df3['Casos M']

In [19]:
df3.query("pais=='Saudi Arabia'")

pais   anio  casos F  Casos M  energia_produccion       co2  casos
3  Saudi Arabia  60105     6494    20066              699.96  10849.67  26560

In [20]:
fig = make_subplots(specs=[[{"secondary_y": True}]])
fig.add_trace(go.Bar(x=df3['pais'],y=df3['co2'],name='CO2'))
fig.add_trace(go.Bar(x=df3['pais'],y=df3['energia_produccion'],base='stack',name='Produccion',opacity=0.6),secondary_y=False)
fig.add_trace(go.Scatter(x=df3['pais'],y=df3['casos'],name='Casos',opacity=0.5),secondary_y=True)
fig.update_layout(go.Layout(
    barmode='overlay'
))
fig.update_layout(title='Consumo vs produccion en top paises productores energia',title_x = 0.4)
fig.show()

In [21]:
df3[['casos','co2']].corr()

casos       co2
casos  1.000000  0.893207
co2    0.893207  1.000000

KPI 2030

In [36]:
df = df_co2[df_co2['energia_tipo']=='all_energy_types']
df = df[['pais','anio','energia_cons','co2','pbi']]

In [23]:
df = df.sort_values(by=['pais','anio']).reset_index(drop=True)

In [24]:
df['pct_chg_co2'] = df['co2'].pct_change(1)*100
df['pct_chg_cons'] = df['energia_cons'].pct_change(1)*100
df = df[df['anio']>=2010]

In [25]:
df_top = df[df['pais'].isin(paises)]

In [26]:
fig = px.line(df_top,x='anio',y='pct_chg_co2',color='pais')
fig.update_layout(title="Porcentaje de cambio en emisiones de CO2, TOP5 paises emisores")
fig.show()

In [27]:
df_kpi_2030 = df.groupby(by=['pais','anio']).sum()
df_kpi_2030 = df_kpi_2030.reset_index()
kpi = df_kpi_2030.loc[df_kpi_2030['anio']==2019,['pais','pct_chg_co2']]
kpi.sort_values(by='pct_chg_co2').head(15)

pais  pct_chg_co2
1399                Mozambique   -27.467412
1229                     Macau   -18.292683
759                      Gabon   -15.681234
189                     Belize   -14.705882
2059                     Tonga   -11.764706
599          Equatorial Guinea   -11.553030
1819                Seychelles   -11.538462
19                     Albania   -10.044643
1239                Madagascar    -8.378378
2289                     Yemen    -8.296460
1739               Saint Lucia    -8.163265
49                      Angola    -7.885117
1759  Saint Vincent/Grenadines    -7.692308
1959                    Sweden    -7.213244
439          Congo-Brazzaville    -7.127883

In [37]:
top_emisores=['United States', 'China', 'Russia', 'Saudi Arabia', 'Canada']

In [28]:
anios = [2010,2019]
df19 = df[df['anio'].isin(anios)][['pais','pbi','anio','co2']]
df19['pct_chg_co2'] = df19['co2'].pct_change(1)*100
df19 = df19[df19['anio']==2019]

df19['cumplimiento']=(df19['pct_chg_co2']+45)/-45*100
df19.sort_values(by='pct_chg_co2').head(15)

pais     pbi  anio    co2  pct_chg_co2  cumplimiento
7639          South Sudan   17.33  2019   1.68   -99.761011    121.691135
239            Antarctica     NaN  2019   0.01   -95.000000    111.111111
6079          North Korea   43.14  2019  20.15   -67.811502     50.692226
5519           Montserrat     NaN  2019   0.03   -62.500000     38.888889
8599  U.S. Virgin Islands    1.88  2019   2.44   -61.022364     35.605254
9159                Yemen   53.08  2019   8.29   -60.429594     34.287987
5679                Nauru     NaN  2019   0.08   -60.000000     33.333333
7919                Syria   53.60  2019  30.96   -49.715771     10.479490
2159             Djibouti    5.85  2019   0.67   -44.166667     -1.851852
359               Armenia   35.56  2019   5.98   -40.438247    -10.137229
159        American Samoa     NaN  2019   0.36   -40.000000    -11.111111
3519                 Guam     NaN  2019   1.83   -37.328767    -17.047184
7319         Sierra Leone   13.85  2019   0.99   -29.285714    -34.920635
6639          Puerto Rico   66.91  2019  20.15   -27.881174    -38.041836
3359               Greece  300.59  2019  73.67   -27.253876    -39.435832

In [78]:
df19.query("pais != 'World'").sort_values(by='co2',ascending=False).head(5)

pais       pbi  anio       co2  pct_chg_co2  cumplimiento
1639          China  23128.34  2019  10608.60    29.307886   -165.128636
8799  United States  19925.43  2019   5277.19    -2.340451    -94.798998
3959          India   9310.29  2019   2308.33    49.256733   -209.459406
6799         Russia   3770.42  2019   1798.24    19.437563   -143.194584
4279          Japan   5359.05  2019   1140.95    -0.343267    -99.237184

In [79]:
top_emision = df19.query("pais != 'World'").sort_values(by='co2',ascending=False).head(5)
top_reduccion = df19.sort_values(by='pct_chg_co2').head(5)
df_pbi = pd.concat([top_emision,top_reduccion])

In [80]:
df_pbi.dropna(subset='pbi',inplace=True)

In [87]:
df_pbi['cumplimiento'] = df_pbi['cumplimiento'].round(2)

In [88]:
df_pbi = df_pbi.sort_values(by='pbi',ascending=False)

In [89]:
title = f"Relacion PBI - cumplimiento de -45% CO2 entre TOP5 emision y TOP5 paises cumplimiento de meta (2019)"

In [90]:
fig = make_subplots(specs=[[{"secondary_y": True}]])
fig.add_trace(go.Bar(x=df_pbi['pais'],y=df_pbi['pbi'],name='PBI'))
fig.add_trace(go.Scatter(x=df_pbi['pais'],y=df_pbi['cumplimiento'],name='Cumplimiento',mode='markers', marker_color=df_pbi['cumplimiento'],),secondary_y=True)
fig.update_layout(title=title)
fig.show()

In [29]:
data = pd.read_csv(r"C:\Users\ferch\Desktop\Henry\Proyecto Grupal\CO2-Emissions\datasets\NORMALIZADO_central_electrica.csv",sep=';')
df_pp = pd.DataFrame(data)

In [30]:
df_pp.drop(columns=col,inplace=True)

In [31]:
df_pp

codigo_iso         pais  \
0             AFG  Afghanistan   
1             AFG  Afghanistan   
2             AFG  Afghanistan   
3             AFG  Afghanistan   
4             AFG  Afghanistan   
...           ...          ...   
244547        ZMB       Zambia   
244548        ZMB       Zambia   
244549        ZMB       Zambia   
244550        ZWE     Zimbabwe   
244551        ZWE     Zimbabwe   

                                                   nombre  capacidad_MW  \
0            Kajaki Hydroelectric Power Plant Afghanistan          33.0   
1                                            Kandahar DOG          10.0   
2                                            Kandahar JOL          10.0   
3           Mahipar Hydroelectric Power Plant Afghanistan          66.0   
4        Naghlu Dam Hydroelectric Power Plant Afghanistan         100.0   
...                                                   ...           ...   
244547                                              Ndola          50.0   
244548                                              Nkana          20.0   
244549                                     Victoria Falls         108.0   
244550                   Hwange Coal Power Plant Zimbabwe         920.0   
244551  Kariba Dam South Hydroelectric Power Station Z...         750.0   

        latitud  longitud energia_primaria otra_energia1  año_apertura  \
0       32.3220   65.1190            Hydro           NaN           NaN   
1       31.6700   65.7950            Solar           NaN           NaN   
2       31.6230   65.7920            Solar           NaN           NaN   
3       34.5560   69.4787            Hydro           NaN           NaN   
4       34.6410   69.7170            Hydro           NaN           NaN   
...         ...       ...              ...           ...           ...   
244547 -12.9667   28.6333              Oil           NaN           NaN   
244548 -12.8167   28.2000              Oil           NaN           NaN   
244549 -17.9167   25.8500            Hydro           NaN           NaN   
244550 -18.3835   26.4700             Coal           NaN           NaN   
244551 -16.5222   28.7619            Hydro           NaN           NaN   

        año_capacidad_reportada  anio  GWh_x_anio  
0                        2017.0  2013         NaN  
1                           NaN  2013         NaN  
2                           NaN  2013         NaN  
3                        2017.0  2013         NaN  
4                        2017.0  2013         NaN  
...                         ...   ...         ...  
244547                      NaN  2019         NaN  
244548                      NaN  2019         NaN  
244549                      NaN  2019         NaN  
244550                   2017.0  2019         NaN  
244551                   2017.0  2019         NaN  

[244552 rows x 12 columns]

In [32]:
contaminantes = ['Gas','Oil','Coal','Petcoke','Waste','Biomass']

In [33]:
df_pp =df_pp[df_pp['energia_primaria'].isin(contaminantes)]

In [93]:
df_pp['text'] = df_pp['nombre'] + ',' + df_pp['pais'] + ', ' + df_pp['energia_primaria'] + '' + 'Capacidad: ' + df_pp['capacidad_MW'].astype(str)

fig = go.Figure(data=go.Scattergeo(
        lon = df_pp['longitud'],
        lat = df_pp['latitud'],
        text = df_pp['text'],
        mode = 'markers',
        marker_color = df_pp['capacidad_MW'], 
        opacity=0.8
        ))

fig.update_layout(
        title = 'Plantas productoras de energia contaminantes',
        title_x = 0.4,
        geo_scope='world',
    )
fig.show()

C:\Users\ferch\AppData\Local\Temp\ipykernel_8892\2887842196.py:1: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

